# Project 3, Part 2, Creating Neo4J Graph DB for our Customers
## Louvain Community
## Centrality Algorithm 
## Minimum Spanning Tree


University of California, Berkeley

Master of Information and Data Science (MIDS) program

w205 - Fundamentals of Data Engineering

Students: 

Edgar Leon, 

Javier Rodriguez, 

Melia Soque, 

Neha Jakkinpali

Year: 2023

Semester:Spring

Section:10


## Web server interface at https://xxxx:7473

#### Update - since the videos were filmed, neo4j requires a longer, more complex password, so the newest password is here:

**Username: neo4j**

**Password: ucb_mids_w205**

The above web server allows and interactive GUI which can output graphs visually in addition to table like output.  The nodes in the graphs can be moved around with the mouse to make the graphs more readable.


#### Basics:

```:server connect``` - connect to the server, username is "neo4j", password is "ucb_mids_w205"


```:server status``` - shows that username and server you are logged into


```:clear``` - clears off old cells


```show databases``` - note that community edition only has 1 application database that we can use neo4j, we cannot create now use other databases, we have to wipe out neo4j database for each new graph

### In the Neo4j GUI, run the following query with graph output and rearrange the nodes with your mouse if necessary:
match (n) return n

# Included Modules and Packages

Code cell containing your includes for modules and packages


In [1]:
import neo4j

import csv

import math
import numpy as np
import pandas as pd

import psycopg2

import gmaps
import gmaps.geojson_geometries

from geographiclib.geodesic import Geodesic
from IPython.display import display

# Supporting code

In [2]:
driver = neo4j.GraphDatabase.driver(uri="neo4j://neo4j:7687", auth=("neo4j","ucb_mids_w205"))

In [3]:
session = driver.session(database="neo4j")

In [4]:
def my_neo4j_wipe_out_database():
    "wipe out database by deleting all nodes and relationships"
    
    query = "match (node)-[relationship]->() delete node, relationship"
    session.run(query)
    
    query = "match (node) delete node"
    session.run(query)

In [5]:
def my_neo4j_run_query_pandas(query, **kwargs):
    "run a query and return the results in a pandas dataframe"
    
    result = session.run(query, **kwargs)
    
    df = pd.DataFrame([r.values() for r in result], columns=result.keys())
    
    return df

In [6]:
def my_neo4j_number_nodes_relationships():
    "print the number of nodes and relationships"
   
    
    query = """
        match (n) 
        return n.name as node_name, labels(n) as labels
        order by n.name
    """
    
    df = my_neo4j_run_query_pandas(query)
    
    number_nodes = df.shape[0]
    
    
    query = """
        match (n1)-[r]->(n2) 
        return n1.name as node_name_1, labels(n1) as node_1_labels, 
            type(r) as relationship_type, n2.name as node_name_2, labels(n2) as node_2_labels
        order by node_name_1, node_name_2
    """
    
    df = my_neo4j_run_query_pandas(query)
    
    number_relationships = df.shape[0]
    
    print("-------------------------")
    print("  Nodes:", number_nodes)
    print("  Relationships:", number_relationships)
    print("-------------------------")


In [7]:
def my_neo4j_create_customer_node(customer_id):
    "create a node with label customer id"
    
    query = """
    
    CREATE (:Customer {name: $customer_id})
    
    """
    
    session.run(query, customer_id=customer_id)
    

In [8]:
def my_neo4j_create_relationship_one_customer(from_customer, to_customer, weight):
    "create a relationship one way between two stations with a weight"
    #weight is in miles from 0 to 0.25, if greater than 1 than it doesnt work
    weight = 1/weight
    query = """
    
    MATCH (from:Customer), 
          (to:Customer)
    WHERE from.name = $from_customer and to.name = $to_customer
    CREATE (from)-[:LINK {weight: $weight}]->(to)
    
    """
    
    session.run(query, from_customer=from_customer, to_customer=to_customer, weight=weight)
    

In [9]:
#
# function to run a select query and return rows in a pandas dataframe
# pandas puts all numeric values from postgres to float
# if it will fit in an integer, change it to integer
#

def my_select_query_pandas(query, rollback_before_flag, rollback_after_flag):
    "function to run a select query and return rows in a pandas dataframe"
    
    if rollback_before_flag:
        connection.rollback()
    
    df = pd.read_sql_query(query, connection)
    
    if rollback_after_flag:
        connection.rollback()
    
    # fix the float columns that really should be integers
    
    for column in df:
    
        if df[column].dtype == "float64":

            fraction_flag = False

            for value in df[column].values:
                
                if not np.isnan(value):
                    if value - math.floor(value) != 0:
                        fraction_flag = True

            if not fraction_flag:
                df[column] = df[column].astype('Int64')
    
    return(df)
    

In [10]:
connection = psycopg2.connect(
    user = "postgres",
    password = "ucb",
    host = "postgres",
    port = "5432",
    database = "postgres"
)

In [11]:
cursor = connection.cursor()

# Wipe out the Neo4j database

Call the function my_neo4j_wipe_out_database() to wipe out the Neo4j database

In [12]:
my_neo4j_wipe_out_database()

# Verify the number of nodes and relationships

In [13]:
my_neo4j_number_nodes_relationships()

-------------------------
  Nodes: 0
  Relationships: 0
-------------------------


# Beggining of Project 3 Code 

# Community Detection 
## Lets use the customer locations and connect them 
## we will use a radius read out, and connect if within a radius
### We will then use the a graph algorithm to generate the customer deployment 'districts'
### After which we shall find a center for the orders for that day

#### 1: Calculate geographic box to look
#### 2: Generate function that generates sql query to detect customers whose location is within the box
#### 3: Add those 'detected' customers to some type of middle stage table or
#### 4: Covert to neo4j graph database 
#### 5: Run algorithhm on datbase to determine if they are a community
#### 6: Generate community clusters (what size is a good cluster size?)
#### 7: Visualize


## Load Customer file from CSV, to save in a Table

## Load Customer file into a Table
## Drop the table berkeley_customers if it exists

In [32]:
connection.rollback()

query = """

drop table if exists berkeley_customers;

"""

cursor.execute(query)

connection.commit()




## Create the table berkeley_customers


In [33]:
connection.rollback()

query = """

create table berkeley_customers(
  Unnamed serial,
  zip varchar(100),
  population int,
  area float,
  density float,
  latitude float,
  longitude float,
  n_lat float,
  n_lon float,
  customer_id varchar(100),
  first_name varchar(100),
  last_name varchar(100),
  street varchar(100),
  city varchar(100),
  state varchar(100),
  closest_store_id varchar(100),
  distance int
  
  );

"""

cursor.execute(query)

connection.commit()


## Load the CSV file cusotmers_w_fake_addresses.csv into the table berkeley_customers


In [34]:
connection.rollback()

query = """


copy berkeley_customers (Unnamed,
  zip,
  population,
  area,
  density,
  latitude,
  longitude,
  n_lat,
  n_lon,
  customer_id,
  first_name,
  last_name,
  street,
  city,
  state,
  closest_store_id,
  distance)

from '/user/projects/project-3-edgaroleon/code/cusotmers_w_fake_addresses.csv' delimiter ',' NULL '' csv header;

"""

cursor.execute(query)

connection.commit()

## Load Customers with Fake Address from Postgres Table Into customers_df dataframe

In [35]:
rollback_before_flag = True
rollback_after_flag = True

query = """


select * 
from berkeley_customers


"""

customers_df =  my_select_query_pandas(query, rollback_before_flag, rollback_after_flag)
customers_df.head()

unnamed    zip  population    area  density  latitude  longitude  \
0        0  94002       27202  5.9244  4591.53   37.5135  -122.2991   
1        1  94002       27202  5.9244  4591.53   37.5135  -122.2991   
2        2  94002       27202  5.9244  4591.53   37.5135  -122.2991   
3        3  94002       27202  5.9244  4591.53   37.5135  -122.2991   
4        4  94005        4692  4.8168   974.09   37.6887  -122.4080   

       n_lat       n_lon customer_id first_name last_name  \
0  37.520606 -122.298226        8103      Karil     Gives   
1  37.513840 -122.289873        8100      Mercy  Blunsden   
2  37.510353 -122.301011        8101      Levey     Duval   
3  37.514176 -122.306404        8102     Margot  MacGiany   
4  37.682348 -122.406707        7158    Malissa     Latek   

                 street      city state closest_store_id  distance  
0      458 Welch Avenue   Belmont    CA                1        24  
1     173 Fairview Pass   Belmont    CA                1        24  
2        512 Melby Hill   Belmont    CA                1        24  
3    12 Fordem Crossing   Belmont    CA                1        24  
4  8346 Fieldstone Park  Brisbane    CA                1        14

## Clean all Nodes and Relationships

In [176]:
my_neo4j_wipe_out_database()

# Building a Graph DB for All Customers That Are Near Each Other

## Query the list of customer_id and create  nodes in the graph for all customers 



In [177]:
import time
start_time = time.time()

connection.rollback()

query = """

select customer_id
from berkeley_customers
order by customer_id

"""

cursor.execute(query)

connection.rollback()

rows = cursor.fetchall()

for row in rows:
    
    customer = row[0]
    
    my_neo4j_create_customer_node(customer)
    
print(time.time() - start_time, " seconds")

22.753582000732422  seconds


## Verify the number of nodes and relationships

In [178]:
my_neo4j_number_nodes_relationships()

-------------------------
  Nodes: 8138
  Relationships: 0
-------------------------


# Query the list of customers and the customers that are nearby 
## What is considered nearby? Nearby is within 0.24 miles or two city blocks.

In Chicago, a typical city block is 330 by 660 feet (100 m × 200 m), which has been adopted by other US cities.

Reference: https://en.wikipedia.org/wiki/City_block#:~:text=Oblong%20blocks%20range%20considerably%20in,adopted%20by%20other%20US%20cities.

## my_calculate_distance() - function to calculate the geodesic distance in miles between two points;  unlike great circle, geodesic takes into account that the earth is an ellipsoid not a sphere

In [14]:
#
#  Given two points in (latitude, longitude) format, calculate the distance between them in miles
#

def my_calculate_distance(point_1, point_2):
    "Given two points in (latitude, longitude) format, calculate the distance between them in miles"    
    geod = Geodesic.WGS84
    g = geod.Inverse(point_1[0], point_1[1], point_2[0], point_2[1])
    miles = g['s12'] / 1000 * 0.621371
    
    return miles

## my_calculate_box() - function that take a point and X miles and finds a box;  left is west X miles; right is X miles east; top is X miles north; bottom is X miles south

In [15]:
#
#  Given a point and miles, calculate the box  
#
#

def my_calculate_block(point, miles):
    "Given a point and a distance in miles, calculate a block with form left, right, top, bottom"
    
    geod = Geodesic.WGS84

    kilometers = miles * 1.60934
    meters = kilometers * 1000

    g = geod.Direct(point[0], point[1], 270, meters)
    left = (g['lat2'], g['lon2'])

    g = geod.Direct(point[0], point[1], 90, meters)
    right = (g['lat2'], g['lon2'])

    g = geod.Direct(point[0], point[1], 0, meters)
    top = (g['lat2'], g['lon2'])

    g = geod.Direct(point[0], point[1], 180, meters)
    bottom = (g['lat2'], g['lon2'])
    
    return(left, right, top, bottom)

In [16]:
#0.125  is 660 feet, pretty masonic/satanic for the US to embed that number into their city planning

sather_gate_berkeley = (37.52060596046, -122.29822615354533)

left, right, top, bottom = my_calculate_block(sather_gate_berkeley, 0.125 )

print (left, right, top, bottom)
type(sather_gate_berkeley )

(37.52060593853792, -122.30050177466813) (37.52060593853792, -122.29595053242252) (37.522418485340395, -122.29822615354533) (37.51879343502199, -122.29822615354533)


tuple

## Lets Put this to Test

In [84]:
rollback_before_flag = True
rollback_after_flag = True

query = """


select * 
from berkeley_customers


"""

customers_df =  my_select_query_pandas(query, rollback_before_flag, rollback_after_flag)
#for customer_id = 8103, retrieve n_lat and n_lon and insert into box function as a tuple
point = (customers_df.loc[customers_df['customer_id'] == '8103']['n_lat'][0], customers_df.loc[customers_df['customer_id'] == '8103']['n_lon'][0])
left, right, top, bottom = my_calculate_block(point, 0.5) #tryy 1/2 mile for now
#customers_df.head()
print(left, right, top, bottom)
#point

(37.52060560970656, -122.3073286380099) (37.52060560970656, -122.28912366908075) (37.527856056635606, -122.29822615354533) (37.513355855362164, -122.29822615354533)


## The box allows us to easily find point stored in a database table

In [85]:
connection.rollback()

#select customer_id
#from berkeley_customers


query = "select customer_id from berkeley_customers "
query += " where n_lat >= " + str(bottom[0])
query += " and n_lat <= " + str(top [0])
query += " and n_lon >= " + str(left[1])
query += " and n_lon <= " + str(right[1])
query += " order by 1 "

cursor.execute(query)

connection.rollback()

rows = cursor.fetchall()

for row in rows:
    print(row[0])


8100
8102
8103


## Lets iterate over all customers

In [179]:
import time
start_time = time.time()






rollback_before_flag = True
rollback_after_flag = True

query = """


select * 
from berkeley_customers


"""

customers_df =  my_select_query_pandas(query, rollback_before_flag, rollback_after_flag)

#for customer_id = 8103, retrieve n_lat and n_lon and insert into box function as a tuple
point = (customers_df.loc[customers_df['customer_id'] == '8103']['n_lat'][0], customers_df.loc[customers_df['customer_id'] == '8103']['n_lon'][0])
left, right, top, bottom = my_calculate_block(point, 0.5) #tryy 1/4 mile for now



block_size = 0.24 #miles
for ind in customers_df.index:
    point = (customers_df['n_lat'][ind], customers_df['n_lon'][ind])
   
    left, right, top, bottom = my_calculate_block(point, block_size) #tryy 1/4 mile for now
    connection.rollback()
    query = "select customer_id from berkeley_customers "
    query += " where n_lat >= " + str(bottom[0])
    query += " and n_lat <= " + str(top [0])
    query += " and n_lon >= " + str(left[1])
    query += " and n_lon <= " + str(right[1])
    query += " order by 1 "
    cursor.execute(query)
    connection.rollback()
    rows = cursor.fetchall()
   
    print("*********"+str(ind)+"*********")
    print("running time ", time.time() - start_time, "seconds")
    for row in rows:        
        if row[0] != customers_df['customer_id'][ind]:
            cid = str(row[0])            
            l_df = customers_df.loc[customers_df['customer_id'] == cid]
            point_1 = ( customers_df['n_lat'][ind], customers_df['n_lon'][ind])
            point_2 = ( float(l_df['n_lat']), float(l_df['n_lon']) )
            weight =  my_calculate_distance(point_1, point_2)
            my_neo4j_create_relationship_one_customer(customers_df['customer_id'][ind], row[0], weight)
            print("created relationship between ", customers_df['customer_id'][ind], "and ", row[0])

print("total execution time ", time.time() - start_time, "seconds")
    
        

*********0*********
*********1*********
*********2*********
*********3*********
*********4*********
created relationship between  7158 and  7162
created relationship between  7158 and  7173
created relationship between  7158 and  7186
created relationship between  7158 and  7189
*********5*********
*********6*********
created relationship between  7192 and  7163
created relationship between  7192 and  7176
created relationship between  7192 and  7178
created relationship between  7192 and  7179
created relationship between  7192 and  7182
*********7*********
created relationship between  7191 and  7170
*********8*********
created relationship between  7190 and  7154
created relationship between  7190 and  7161
created relationship between  7190 and  7175
created relationship between  7190 and  7182
*********9*********
created relationship between  7189 and  7155
created relationship between  7189 and  7158
created relationship between  7189 and  7164
created relationship between  7189 

created relationship between  7558 and  7535
created relationship between  7558 and  7551
created relationship between  7558 and  7552
created relationship between  7558 and  7553
created relationship between  7558 and  7560
*********58*********
created relationship between  7559 and  7544
*********59*********
created relationship between  7561 and  7523
created relationship between  7561 and  7526
created relationship between  7561 and  7527
created relationship between  7561 and  7529
created relationship between  7561 and  7534
created relationship between  7561 and  7551
created relationship between  7561 and  7554
*********60*********
created relationship between  7543 and  7525
created relationship between  7543 and  7540
created relationship between  7543 and  7546
created relationship between  7543 and  7549
*********61*********
created relationship between  7544 and  7540
created relationship between  7544 and  7555
created relationship between  7544 and  7559
created relation

created relationship between  7946 and  7944
*********136*********
created relationship between  7945 and  7941
*********137*********
*********138*********
*********139*********
*********140*********
*********141*********
*********142*********
*********143*********
*********144*********
*********145*********
created relationship between  7831 and  7824
*********146*********
created relationship between  7830 and  7824
*********147*********
created relationship between  7824 and  7830
created relationship between  7824 and  7831
*********148*********
created relationship between  5406 and  5374
created relationship between  5406 and  5378
created relationship between  5406 and  5382
created relationship between  5406 and  5383
created relationship between  5406 and  5390
created relationship between  5406 and  5395
created relationship between  5406 and  5400
created relationship between  5406 and  5413
created relationship between  5406 and  5418
created relationship between  5406 and 

created relationship between  5446 and  5654
created relationship between  5446 and  5658
created relationship between  5446 and  5663
created relationship between  5446 and  5708
created relationship between  5446 and  5732
created relationship between  5446 and  5994
created relationship between  5446 and  6014
created relationship between  5446 and  6034
created relationship between  5446 and  6035
*********159*********
created relationship between  5447 and  5371
created relationship between  5447 and  5372
created relationship between  5447 and  5374
created relationship between  5447 and  5376
created relationship between  5447 and  5378
created relationship between  5447 and  5382
created relationship between  5447 and  5383
created relationship between  5447 and  5386
created relationship between  5447 and  5390
created relationship between  5447 and  5395
created relationship between  5447 and  5400
created relationship between  5447 and  5404
created relationship between  544

created relationship between  5420 and  5519
*********170*********
created relationship between  5419 and  5411
created relationship between  5419 and  5414
created relationship between  5419 and  5991
created relationship between  5419 and  6435
*********171*********
created relationship between  5418 and  5371
created relationship between  5418 and  5374
created relationship between  5418 and  5375
created relationship between  5418 and  5378
created relationship between  5418 and  5382
created relationship between  5418 and  5383
created relationship between  5418 and  5386
created relationship between  5418 and  5390
created relationship between  5418 and  5400
created relationship between  5418 and  5404
created relationship between  5418 and  5406
created relationship between  5418 and  5413
created relationship between  5418 and  5423
created relationship between  5418 and  5425
created relationship between  5418 and  5427
created relationship between  5418 and  5434
created rel

...

created relationship between  6374 and  6392
created relationship between  6374 and  6397
created relationship between  6374 and  6400
*********7939*********
created relationship between  6375 and  6330
created relationship between  6375 and  6332
created relationship between  6375 and  6342
created relationship between  6375 and  6344
created relationship between  6375 and  6355
created relationship between  6375 and  6365
created relationship between  6375 and  6369
created relationship between  6375 and  6374
created relationship between  6375 and  6391
created relationship between  6375 and  6400
*********7940*********
created relationship between  6376 and  6329
created relationship between  6376 and  6333
created relationship between  6376 and  6335
created relationship between  6376 and  6340
created relationship between  6376 and  6352
created relationship between  6376 and  6360
created relationship between  6376 and  6367
created relationship between  6376 and  6378
created r

created relationship between  6382 and  6397
*********7957*********
created relationship between  6383 and  6333
created relationship between  6383 and  6345
created relationship between  6383 and  6346
*********7958*********
created relationship between  6384 and  6336
created relationship between  6384 and  6380
*********7959*********
created relationship between  6385 and  6329
created relationship between  6385 and  6339
created relationship between  6385 and  6340
created relationship between  6385 and  6343
created relationship between  6385 and  6351
created relationship between  6385 and  6360
created relationship between  6385 and  6371
created relationship between  6385 and  6389
created relationship between  6385 and  6396
created relationship between  6385 and  6402
*********7960*********
created relationship between  6386 and  6333
created relationship between  6386 and  6335
created relationship between  6386 and  6348
created relationship between  6386 and  6354
created 

created relationship between  7810 and  7808
created relationship between  7810 and  7809
created relationship between  7810 and  7816
*********7982*********
*********7983*********
created relationship between  7812 and  7798
created relationship between  7812 and  7813
created relationship between  7812 and  7818
created relationship between  7812 and  7822
*********7984*********
created relationship between  7813 and  7798
created relationship between  7813 and  7812
created relationship between  7813 and  7818
created relationship between  7813 and  7822
*********7985*********
created relationship between  7814 and  7792
created relationship between  7814 and  7795
created relationship between  7814 and  7817
*********7986*********
created relationship between  7815 and  7789
created relationship between  7815 and  7794
created relationship between  7815 and  7803
created relationship between  7815 and  7806
created relationship between  7815 and  7807
created relationship between  

created relationship between  7503 and  7508
created relationship between  7503 and  7510
created relationship between  7503 and  7514
created relationship between  7503 and  7515
created relationship between  7503 and  7518
created relationship between  7503 and  7520
*********8059*********
created relationship between  7502 and  7489
created relationship between  7502 and  7497
*********8060*********
*********8061*********
created relationship between  7500 and  7801
*********8062*********
created relationship between  7499 and  7508
created relationship between  7499 and  7513
created relationship between  7499 and  7518
created relationship between  7499 and  7519
created relationship between  7499 and  7521
*********8063*********
created relationship between  7498 and  7503
created relationship between  7498 and  7505
created relationship between  7498 and  7508
created relationship between  7498 and  7510
created relationship between  7498 and  7514
created relationship between  

created relationship between  7451 and  7460
created relationship between  7451 and  7481
*********8103*********
created relationship between  7452 and  7464
created relationship between  7452 and  7487
*********8104*********
created relationship between  7458 and  7457
created relationship between  7458 and  7463
created relationship between  7458 and  7469
created relationship between  7458 and  7470
created relationship between  7458 and  7471
created relationship between  7458 and  7472
created relationship between  7458 and  7475
created relationship between  7458 and  7485
*********8105*********
created relationship between  7459 and  7477
*********8106*********
created relationship between  7460 and  7451
created relationship between  7460 and  7482
*********8107*********
created relationship between  7461 and  7455
created relationship between  7461 and  7481
*********8108*********
created relationship between  7462 and  7457
created relationship between  7462 and  7472
created

In [180]:
my_neo4j_number_nodes_relationships()

-------------------------
  Nodes: 8138
  Relationships: 133111
-------------------------


# Detecting Louvain Communities


In [208]:
query = "CALL gds.graph.drop('ds_graph', false)"
session.run(query)

query = """
CALL gds.graph.project('ds_graph', 'Customer', 'LINK', 
                      {relationshipProperties: 'weight'})

"""

session.run(query)




### Tried several groups,  but for a block_size of 0.24 miles it yields 515 total groups with an average member size per group of: 15
  

In [210]:
query = """

CALL gds.louvain.stream('ds_graph')
YIELD nodeId, communityId, intermediateCommunityIds
RETURN gds.util.asNode(nodeId).name AS name, communityId as community, intermediateCommunityIds as intermediate_community
ORDER BY community, name ASC

"""

clusters_df = my_neo4j_run_query_pandas(query)
clusters_df

name  community intermediate_community
0     1022        173                   None
1     1023        173                   None
2     1024        173                   None
3     1025        173                   None
4     1027        173                   None
...    ...        ...                    ...
8133   995       7953                   None
8134   996       7953                   None
8135   997       7953                   None
8136   998       7953                   None
8137   999       7953                   None

[8138 rows x 3 columns]

In [218]:
g = clusters_df.community.unique()
g.shape

(515,)

## Merge clusters_df community and customers_df 

In [221]:
customers_df.head()
customers2_df = customers_df[["zip", "n_lat", "n_lon", "customer_id", "first_name", "last_name", "street", "city"]]
customers2_df.head()



zip      n_lat       n_lon customer_id first_name last_name  \
0  94002  37.520606 -122.298226        8103      Karil     Gives   
1  94002  37.513840 -122.289873        8100      Mercy  Blunsden   
2  94002  37.510353 -122.301011        8101      Levey     Duval   
3  94002  37.514176 -122.306404        8102     Margot  MacGiany   
4  94005  37.682348 -122.406707        7158    Malissa     Latek   

                 street      city  
0      458 Welch Avenue   Belmont  
1     173 Fairview Pass   Belmont  
2        512 Melby Hill   Belmont  
3    12 Fordem Crossing   Belmont  
4  8346 Fieldstone Park  Brisbane

## Insert community column 

In [ ]:
customers2_df.insert(7, 'louvein_community',clusters_df['community'] )


In [238]:
customers2_df

zip      n_lat       n_lon customer_id first_name last_name  \
0     94002  37.520606 -122.298226        8103      Karil     Gives   
1     94002  37.513840 -122.289873        8100      Mercy  Blunsden   
2     94002  37.510353 -122.301011        8101      Levey     Duval   
3     94002  37.514176 -122.306404        8102     Margot  MacGiany   
4     94005  37.682348 -122.406707        7158    Malissa     Latek   
...     ...        ...         ...         ...        ...       ...   
8133  94973  38.006360 -122.638831        8098      Luisa   Symcoxe   
8134  94973  38.017764 -122.637123        8099     Adella   Buscher   
8135  94973  38.003338 -122.627826        8094      Raviv   Pierton   
8136  94973  38.011278 -122.641591        8093      Lemmy  Ettridge   
8137  94973  38.008756 -122.641346        8095      Emmet   Phippin   

                      street  louvein_community      city  
0           458 Welch Avenue                173   Belmont  
1          173 Fairview Pass                173   Belmont  
2             512 Melby Hill                173   Belmont  
3         12 Fordem Crossing                173   Belmont  
4       8346 Fieldstone Park                173  Brisbane  
...                      ...                ...       ...  
8133     291 Thompson Street               7953  Woodacre  
8134     20 Scofield Parkway               7953  Woodacre  
8135     5739 Holmberg Point               7953  Woodacre  
8136         24 Dahle Circle               7953  Woodacre  
8137  78379 Fieldstone Trail               7953  Woodacre  

[8138 rows x 9 columns]

In [268]:
s = clusters_df.loc[clusters_df['name'] == customers2_df['customer_id'][1]]
customers2_df.loc[ customers2_df['customer_id'] == customers2_df['customer_id'][1], 'louvein_community'] = int(s['community'])

customers2_df.head()


zip      n_lat       n_lon customer_id first_name last_name  \
0  94002  37.520606 -122.298226        8103      Karil     Gives   
1  94002  37.513840 -122.289873        8100      Mercy  Blunsden   
2  94002  37.510353 -122.301011        8101      Levey     Duval   
3  94002  37.514176 -122.306404        8102     Margot  MacGiany   
4  94005  37.682348 -122.406707        7158    Malissa     Latek   

                 street louvein_community      city  
0      458 Welch Avenue               173   Belmont  
1     173 Fairview Pass              7891   Belmont  
2        512 Melby Hill               173   Belmont  
3    12 Fordem Crossing               173   Belmont  
4  8346 Fieldstone Park               173  Brisbane

In [271]:
for ind in customers2_df.index:
    s = clusters_df.loc[clusters_df['name'] == customers2_df['customer_id'][ind]] #gets me the customer_id dataframe in s
    customers2_df.loc[ customers2_df['customer_id'] == customers2_df['customer_id'][ind], 'louvein_community'] = int(s['community'])

customers2_df.head()

zip      n_lat       n_lon customer_id first_name last_name  \
0  94002  37.520606 -122.298226        8103      Karil     Gives   
1  94002  37.513840 -122.289873        8100      Mercy  Blunsden   
2  94002  37.510353 -122.301011        8101      Levey     Duval   
3  94002  37.514176 -122.306404        8102     Margot  MacGiany   
4  94005  37.682348 -122.406707        7158    Malissa     Latek   

                 street louvein_community      city  
0      458 Welch Avenue              7894   Belmont  
1     173 Fairview Pass              7891   Belmont  
2        512 Melby Hill              7892   Belmont  
3    12 Fordem Crossing              7893   Belmont  
4  8346 Fieldstone Park              6860  Brisbane

### Need to do some checking that tables were joined correctly

In [275]:
for ind in customers2_df.index:
    s = clusters_df.loc[clusters_df['name'] == customers2_df['customer_id'][ind]] #gets me the customer_id dataframe in s
    if(customers2_df['louvein_community'][ind] != int(s['community'])):
        print("did not copy correctly")
        print("customer_id: ", customers2_df['louvein_community'][ind] ," community:", int(s['community'])  )
        break
    else: 
        print("matches! customer_id: ", customers2_df['louvein_community'][ind] ," community:", int(s['community'])  )



matches! customer_id:  7894  community: 7894
matches! customer_id:  7891  community: 7891
matches! customer_id:  7892  community: 7892
matches! customer_id:  7893  community: 7893
matches! customer_id:  6860  community: 6860
matches! customer_id:  6882  community: 6882
matches! customer_id:  6881  community: 6881
matches! customer_id:  6881  community: 6881
matches! customer_id:  6881  community: 6881
matches! customer_id:  6860  community: 6860
matches! customer_id:  6860  community: 6860
matches! customer_id:  6881  community: 6881
matches! customer_id:  6860  community: 6860
matches! customer_id:  6881  community: 6881
matches! customer_id:  6872  community: 6872
matches! customer_id:  6881  community: 6881
matches! customer_id:  6881  community: 6881
matches! customer_id:  6860  community: 6860
matches! customer_id:  6860  community: 6860
matches! customer_id:  6881  community: 6881
matches! customer_id:  6881  community: 6881
matches! customer_id:  6881  community: 6881
matches! c

matches! customer_id:  5021  community: 5021
matches! customer_id:  5021  community: 5021
matches! customer_id:  5021  community: 5021
matches! customer_id:  5021  community: 5021
matches! customer_id:  5021  community: 5021
matches! customer_id:  5021  community: 5021
matches! customer_id:  5021  community: 5021
matches! customer_id:  5021  community: 5021
matches! customer_id:  5021  community: 5021
matches! customer_id:  5021  community: 5021
matches! customer_id:  5021  community: 5021
matches! customer_id:  5021  community: 5021
matches! customer_id:  5021  community: 5021
matches! customer_id:  5021  community: 5021
matches! customer_id:  5021  community: 5021
matches! customer_id:  5021  community: 5021
matches! customer_id:  5021  community: 5021
matches! customer_id:  5021  community: 5021
matches! customer_id:  5488  community: 5488
matches! customer_id:  5021  community: 5021
matches! customer_id:  5021  community: 5021
matches! customer_id:  5021  community: 5021
matches! c

matches! customer_id:  5021  community: 5021
matches! customer_id:  5021  community: 5021
matches! customer_id:  5021  community: 5021
matches! customer_id:  5021  community: 5021
matches! customer_id:  5021  community: 5021
matches! customer_id:  5021  community: 5021
matches! customer_id:  5021  community: 5021
matches! customer_id:  5021  community: 5021
matches! customer_id:  5021  community: 5021
matches! customer_id:  5021  community: 5021
matches! customer_id:  5021  community: 5021
matches! customer_id:  5021  community: 5021
matches! customer_id:  5021  community: 5021
matches! customer_id:  5021  community: 5021
matches! customer_id:  5021  community: 5021
matches! customer_id:  5021  community: 5021
matches! customer_id:  5021  community: 5021
matches! customer_id:  5021  community: 5021
matches! customer_id:  5021  community: 5021
matches! customer_id:  5021  community: 5021
matches! customer_id:  5578  community: 5578
matches! customer_id:  5578  community: 5578
matches! c

matches! customer_id:  6911  community: 6911
matches! customer_id:  6911  community: 6911
matches! customer_id:  6918  community: 6918
matches! customer_id:  6911  community: 6911
matches! customer_id:  6911  community: 6911
matches! customer_id:  6911  community: 6911
matches! customer_id:  6911  community: 6911
matches! customer_id:  6911  community: 6911
matches! customer_id:  6911  community: 6911
matches! customer_id:  6911  community: 6911
matches! customer_id:  6911  community: 6911
matches! customer_id:  6911  community: 6911
matches! customer_id:  6911  community: 6911
matches! customer_id:  6918  community: 6918
matches! customer_id:  6911  community: 6911
matches! customer_id:  6911  community: 6911
matches! customer_id:  6911  community: 6911
matches! customer_id:  6491  community: 6491
matches! customer_id:  5021  community: 5021
matches! customer_id:  6491  community: 6491
matches! customer_id:  6491  community: 6491
matches! customer_id:  6491  community: 6491
matches! c

matches! customer_id:  6491  community: 6491
matches! customer_id:  6491  community: 6491
matches! customer_id:  6491  community: 6491
matches! customer_id:  6151  community: 6151
matches! customer_id:  6151  community: 6151
matches! customer_id:  6491  community: 6491
matches! customer_id:  6491  community: 6491
matches! customer_id:  6151  community: 6151
matches! customer_id:  6151  community: 6151
matches! customer_id:  6151  community: 6151
matches! customer_id:  6151  community: 6151
matches! customer_id:  6151  community: 6151
matches! customer_id:  6491  community: 6491
matches! customer_id:  6151  community: 6151
matches! customer_id:  6151  community: 6151
matches! customer_id:  6151  community: 6151
matches! customer_id:  6151  community: 6151
matches! customer_id:  6151  community: 6151
matches! customer_id:  6151  community: 6151
matches! customer_id:  6151  community: 6151
matches! customer_id:  6151  community: 6151
matches! customer_id:  6151  community: 6151
matches! c

...

matches! customer_id:  377  community: 377
matches! customer_id:  377  community: 377
matches! customer_id:  377  community: 377
matches! customer_id:  377  community: 377
matches! customer_id:  377  community: 377
matches! customer_id:  173  community: 173
matches! customer_id:  377  community: 377
matches! customer_id:  377  community: 377
matches! customer_id:  377  community: 377
matches! customer_id:  377  community: 377
matches! customer_id:  377  community: 377
matches! customer_id:  377  community: 377
matches! customer_id:  377  community: 377
matches! customer_id:  173  community: 173
matches! customer_id:  381  community: 381
matches! customer_id:  377  community: 377
matches! customer_id:  173  community: 173
matches! customer_id:  377  community: 377
matches! customer_id:  377  community: 377
matches! customer_id:  377  community: 377
matches! customer_id:  377  community: 377
matches! customer_id:  1037  community: 1037
matches! customer_id:  173  community: 173
matches! 

matches! customer_id:  3596  community: 3596
matches! customer_id:  3463  community: 3463
matches! customer_id:  3463  community: 3463
matches! customer_id:  3463  community: 3463
matches! customer_id:  3463  community: 3463
matches! customer_id:  3463  community: 3463
matches! customer_id:  3463  community: 3463
matches! customer_id:  3463  community: 3463
matches! customer_id:  3463  community: 3463
matches! customer_id:  3463  community: 3463
matches! customer_id:  3463  community: 3463
matches! customer_id:  3463  community: 3463
matches! customer_id:  3463  community: 3463
matches! customer_id:  3463  community: 3463
matches! customer_id:  3463  community: 3463
matches! customer_id:  3463  community: 3463
matches! customer_id:  3463  community: 3463
matches! customer_id:  3463  community: 3463
matches! customer_id:  3463  community: 3463
matches! customer_id:  3463  community: 3463
matches! customer_id:  3463  community: 3463
matches! customer_id:  3463  community: 3463
matches! c

matches! customer_id:  3290  community: 3290
matches! customer_id:  3290  community: 3290
matches! customer_id:  3290  community: 3290
matches! customer_id:  3290  community: 3290
matches! customer_id:  3290  community: 3290
matches! customer_id:  3290  community: 3290
matches! customer_id:  3290  community: 3290
matches! customer_id:  3290  community: 3290
matches! customer_id:  3290  community: 3290
matches! customer_id:  3290  community: 3290
matches! customer_id:  3290  community: 3290
matches! customer_id:  3290  community: 3290
matches! customer_id:  3279  community: 3279
matches! customer_id:  3290  community: 3290
matches! customer_id:  3290  community: 3290
matches! customer_id:  3290  community: 3290
matches! customer_id:  3290  community: 3290
matches! customer_id:  3290  community: 3290
matches! customer_id:  3290  community: 3290
matches! customer_id:  3290  community: 3290
matches! customer_id:  3290  community: 3290
matches! customer_id:  3290  community: 3290
matches! c

matches! customer_id:  5414  community: 5414
matches! customer_id:  5414  community: 5414
matches! customer_id:  5414  community: 5414
matches! customer_id:  5414  community: 5414
matches! customer_id:  5414  community: 5414
matches! customer_id:  5414  community: 5414
matches! customer_id:  5414  community: 5414
matches! customer_id:  5414  community: 5414
matches! customer_id:  5414  community: 5414
matches! customer_id:  5414  community: 5414
matches! customer_id:  5414  community: 5414
matches! customer_id:  5428  community: 5428
matches! customer_id:  5414  community: 5414
matches! customer_id:  5414  community: 5414
matches! customer_id:  5414  community: 5414
matches! customer_id:  5414  community: 5414
matches! customer_id:  5414  community: 5414
matches! customer_id:  5414  community: 5414
matches! customer_id:  5414  community: 5414
matches! customer_id:  5414  community: 5414
matches! customer_id:  5414  community: 5414
matches! customer_id:  5396  community: 5396
matches! c

matches! customer_id:  7230  community: 7230
matches! customer_id:  7230  community: 7230
matches! customer_id:  7230  community: 7230
matches! customer_id:  7230  community: 7230
matches! customer_id:  7230  community: 7230
matches! customer_id:  7230  community: 7230
matches! customer_id:  7230  community: 7230
matches! customer_id:  7230  community: 7230
matches! customer_id:  7230  community: 7230
matches! customer_id:  7225  community: 7225
matches! customer_id:  7550  community: 7550
matches! customer_id:  7230  community: 7230
matches! customer_id:  7230  community: 7230
matches! customer_id:  7230  community: 7230
matches! customer_id:  7230  community: 7230
matches! customer_id:  7230  community: 7230
matches! customer_id:  7230  community: 7230
matches! customer_id:  7215  community: 7215
matches! customer_id:  7545  community: 7545
matches! customer_id:  7230  community: 7230
matches! customer_id:  7230  community: 7230
matches! customer_id:  7230  community: 7230
matches! c

# Store in csv file for later use

In [280]:
import csv
customers2_df.to_csv("customer_louvein_community.csv")

# Store in a posgress table for later use

## Drop the Table if it exists, Table: customer_clusters

In [282]:
connection.rollback()

query = """

drop table if exists customer_clusters;

"""

cursor.execute(query)

connection.commit()


## Create Table 

In [277]:
customers2_df.head()

zip      n_lat       n_lon customer_id first_name last_name  \
0  94002  37.520606 -122.298226        8103      Karil     Gives   
1  94002  37.513840 -122.289873        8100      Mercy  Blunsden   
2  94002  37.510353 -122.301011        8101      Levey     Duval   
3  94002  37.514176 -122.306404        8102     Margot  MacGiany   
4  94005  37.682348 -122.406707        7158    Malissa     Latek   

                 street louvein_community      city  
0      458 Welch Avenue              7894   Belmont  
1     173 Fairview Pass              7891   Belmont  
2        512 Melby Hill              7892   Belmont  
3    12 Fordem Crossing              7893   Belmont  
4  8346 Fieldstone Park              6860  Brisbane

In [283]:
connection.rollback()

query = """

create table customer_clusters(
  unnamed serial,
  zip varchar(100),
  n_lat float,
  n_lon float,
  customer_id varchar(100),
  first_name varchar(100),
  last_name varchar(100),
  street varchar(100),
  louvein_community int,
  city varchar(100)
  
  
  );

"""

cursor.execute(query)

connection.commit()


## Load the Table

In [284]:
connection.rollback()

query = """


copy customer_clusters (
 unnamed,
 zip,
 n_lat,
 n_lon,
 customer_id,
 first_name,
 last_name,
 street,
 louvein_community,
 city
 )

from '/user/projects/project-3-edgaroleon/code/customer_louvein_community.csv' delimiter ',' NULL '' csv header;

"""

cursor.execute(query)

connection.commit()


In [25]:
rollback_before_flag = True
rollback_after_flag = True

query = """


select * 
from customer_clusters


"""

customer_clusters_df =  my_select_query_pandas(query, rollback_before_flag, rollback_after_flag)
customer_clusters_df

unnamed    zip      n_lat       n_lon customer_id first_name last_name  \
0           0  94002  37.520606 -122.298226        8103      Karil     Gives   
1           1  94002  37.513840 -122.289873        8100      Mercy  Blunsden   
2           2  94002  37.510353 -122.301011        8101      Levey     Duval   
3           3  94002  37.514176 -122.306404        8102     Margot  MacGiany   
4           4  94005  37.682348 -122.406707        7158    Malissa     Latek   
...       ...    ...        ...         ...         ...        ...       ...   
8133     8133  94973  38.006360 -122.638831        8098      Luisa   Symcoxe   
8134     8134  94973  38.017764 -122.637123        8099     Adella   Buscher   
8135     8135  94973  38.003338 -122.627826        8094      Raviv   Pierton   
8136     8136  94973  38.011278 -122.641591        8093      Lemmy  Ettridge   
8137     8137  94973  38.008756 -122.641346        8095      Emmet   Phippin   

                      street  louvein_community      city  
0           458 Welch Avenue               7894   Belmont  
1          173 Fairview Pass               7891   Belmont  
2             512 Melby Hill               7892   Belmont  
3         12 Fordem Crossing               7893   Belmont  
4       8346 Fieldstone Park               6860  Brisbane  
...                      ...                ...       ...  
8133     291 Thompson Street               7884  Woodacre  
8134     20 Scofield Parkway               7888  Woodacre  
8135     5739 Holmberg Point               7883  Woodacre  
8136         24 Dahle Circle               7884  Woodacre  
8137  78379 Fieldstone Trail               7884  Woodacre  

[8138 rows x 10 columns]

# Create a Subgroup To Run The Centrality Algorithm On It
## I picked label 6860, but this will depend on orders for that day

In [26]:
central_df = customer_clusters_df.loc[customer_clusters_df['louvein_community'] == 6860]
central_df

unnamed    zip      n_lat       n_lon customer_id first_name    last_name  \
4         4  94005  37.682348 -122.406707        7158    Malissa        Latek   
9         9  94005  37.683216 -122.409611        7189       Kaja     Killiner   
10       10  94005  37.682674 -122.414409        7188     Trever         Wais   
12       12  94005  37.683365 -122.407019        7186     Lucius        Gawne   
17       17  94005  37.686030 -122.410622        7181     Fraser       Vasser   
18       18  94005  37.687203 -122.409959        7180     Candie        Dayne   
25       25  94005  37.682012 -122.403878        7173    Joshuah    MacFadzan   
26       26  94005  37.682657 -122.411316        7172   Francois       Farish   
27       27  94005  37.681886 -122.416236        7171     Byrann      Feechum   
30       30  94005  37.682597 -122.398976        7168      Ashly       Lindup   
32       32  94005  37.679975 -122.412504        7166       Riva  Schoolcroft   
34       34  94005  37.682768 -122.412029        7164     Mellie    Berriball   
36       36  94005  37.680983 -122.403332        7162    Laurena        Calan   
41       41  94005  37.685899 -122.410254        7155      Sonya        Puzey   

                    street  louvein_community      city  
4     8346 Fieldstone Park               6860  Brisbane  
9   2122 Eagle Crest Plaza               6860  Brisbane  
10   13540 Manitowish Lane               6860  Brisbane  
12       6586 Dorton Alley               6860  Brisbane  
17     6313 Warbler Circle               6860  Brisbane  
18           807 Roth Road               6860  Brisbane  
25      135 Di Loreto Park               6860  Brisbane  
26           1 Texas Trail               6860  Brisbane  
27            5 Tony Plaza               6860  Brisbane  
30   47 Fieldstone Parkway               6860  Brisbane  
32   64581 Atwood Junction               6860  Brisbane  
34        85524 Carey Lane               6860  Brisbane  
36     75869 Mccormick Way               6860  Brisbane  
41       3927 Spenser Pass               6860  Brisbane

## Wipe out nodes and relationships

In [300]:
my_neo4j_number_nodes_relationships()

-------------------------
  Nodes: 0
  Relationships: 0
-------------------------


In [301]:
my_neo4j_wipe_out_database()

In [302]:
my_neo4j_number_nodes_relationships()

-------------------------
  Nodes: 0
  Relationships: 0
-------------------------


## Create customer nodes

In [313]:
import time
start_time = time.time()


for ind in central_df.index:
    
    customer = central_df['customer_id'][ind]
    
    my_neo4j_create_customer_node(customer)
    
print(time.time() - start_time, " seconds")

0.04659318923950195  seconds


In [314]:
my_neo4j_number_nodes_relationships()

-------------------------
  Nodes: 14
  Relationships: 0
-------------------------


## Recreate relationship, and use same criteria of distance and weight 

In [315]:
import time
start_time = time.time()


block_size = 0.24 #miles
for ind in central_df.index:
    point = (central_df['n_lat'][ind], central_df['n_lon'][ind])
    left, right, top, bottom = my_calculate_block(point, block_size) #tryy 0.25 mile for now
    
    connection.rollback()
    query = "select customer_id from customer_clusters"
    query += " where n_lat >= " + str(bottom[0])
    query += " and n_lat <= " + str(top [0])
    query += " and n_lon >= " + str(left[1])
    query += " and n_lon <= " + str(right[1])
    query += " order by 1 "
    cursor.execute(query)
    connection.rollback()
    rows = cursor.fetchall()
    print("*********"+str(ind)+"*********")
    print("running time ", time.time() - start_time, "seconds")
    for row in rows:        
        if row[0] != central_df['customer_id'][ind]:
            cid = str(row[0])            
            l_df = central_df.loc[central_df['customer_id'] == cid]
            point_1 = ( central_df['n_lat'][ind], central_df['n_lon'][ind])
            point_2 = ( float(l_df['n_lat']), float(l_df['n_lon']) )
            weight =  my_calculate_distance(point_1, point_2)
            my_neo4j_create_relationship_one_customer(central_df['customer_id'][ind], row[0], weight)
            print("created relationship between ", central_df['customer_id'][ind], "and ", row[0])

print("total execution time ", time.time() - start_time, "seconds")

*********4*********
running time  0.0023956298828125 seconds
created relationship between  7158 and  7162
created relationship between  7158 and  7173
created relationship between  7158 and  7186
created relationship between  7158 and  7189
*********9*********
running time  0.05775761604309082 seconds
created relationship between  7189 and  7155
created relationship between  7189 and  7158
created relationship between  7189 and  7164
created relationship between  7189 and  7166
created relationship between  7189 and  7172
created relationship between  7189 and  7181
created relationship between  7189 and  7186
*********10*********
running time  0.08759760856628418 seconds
created relationship between  7188 and  7155
created relationship between  7188 and  7164
created relationship between  7188 and  7166
created relationship between  7188 and  7171
created relationship between  7188 and  7172
created relationship between  7188 and  7181
*********12*********
running time  0.112164258956

In [316]:
my_neo4j_number_nodes_relationships()

-------------------------
  Nodes: 14
  Relationships: 70
-------------------------


## Run Degree Centrality Algorithm & Results

In [317]:
query = "CALL gds.graph.drop('ds_graph', false)"
session.run(query)

query = """
CALL gds.graph.project('ds_graph', 'Customer', 'LINK', 
                      {relationshipProperties: 'weight'})

"""

session.run(query)

In [319]:
query = """

CALL gds.degree.stream('ds_graph')
YIELD nodeId, score
RETURN gds.util.asNode(nodeId).name AS name, score as degree
ORDER BY degree DESC, name

"""

degree_results_df = my_neo4j_run_query_pandas(query)
degree_results_df

name  degree
0   7155     7.0
1   7164     7.0
2   7172     7.0
3   7181     7.0
4   7186     7.0
5   7189     7.0
6   7188     6.0
7   7166     5.0
8   7158     4.0
9   7162     4.0
10  7171     3.0
11  7173     3.0
12  7180     2.0
13  7168     1.0

In [338]:
#degree_results_df['degree'].max()
temp_df = degree_results_df.loc[degree_results_df['degree'] == degree_results_df['degree'].max()]
max_df = temp_df.sample()
str(int(max_df['name']))

'7186'

### Insert to dataframe, label central node, export to CSV and save

In [341]:
central_df.insert(10, 'central_node',0 )
central_df

unnamed    zip      n_lat       n_lon customer_id first_name    last_name  \
4         4  94005  37.682348 -122.406707        7158    Malissa        Latek   
9         9  94005  37.683216 -122.409611        7189       Kaja     Killiner   
10       10  94005  37.682674 -122.414409        7188     Trever         Wais   
12       12  94005  37.683365 -122.407019        7186     Lucius        Gawne   
17       17  94005  37.686030 -122.410622        7181     Fraser       Vasser   
18       18  94005  37.687203 -122.409959        7180     Candie        Dayne   
25       25  94005  37.682012 -122.403878        7173    Joshuah    MacFadzan   
26       26  94005  37.682657 -122.411316        7172   Francois       Farish   
27       27  94005  37.681886 -122.416236        7171     Byrann      Feechum   
30       30  94005  37.682597 -122.398976        7168      Ashly       Lindup   
32       32  94005  37.679975 -122.412504        7166       Riva  Schoolcroft   
34       34  94005  37.682768 -122.412029        7164     Mellie    Berriball   
36       36  94005  37.680983 -122.403332        7162    Laurena        Calan   
41       41  94005  37.685899 -122.410254        7155      Sonya        Puzey   

                    street  louvein_community      city  central_node  
4     8346 Fieldstone Park               6860  Brisbane             0  
9   2122 Eagle Crest Plaza               6860  Brisbane             0  
10   13540 Manitowish Lane               6860  Brisbane             0  
12       6586 Dorton Alley               6860  Brisbane             0  
17     6313 Warbler Circle               6860  Brisbane             0  
18           807 Roth Road               6860  Brisbane             0  
25      135 Di Loreto Park               6860  Brisbane             0  
26           1 Texas Trail               6860  Brisbane             0  
27            5 Tony Plaza               6860  Brisbane             0  
30   47 Fieldstone Parkway               6860  Brisbane             0  
32   64581 Atwood Junction               6860  Brisbane             0  
34        85524 Carey Lane               6860  Brisbane             0  
36     75869 Mccormick Way               6860  Brisbane             0  
41       3927 Spenser Pass               6860  Brisbane             0

In [343]:
temp_df = degree_results_df.loc[degree_results_df['degree'] == degree_results_df['degree'].max()]
max_df = temp_df.sample()
central_id = str(int(max_df['name']))

central_df.loc[ central_df['customer_id'] == central_id, 'central_node'] = 1

temp2_df = central_df.loc[central_df['customer_id'] == central_id]
temp2_df


/opt/conda/lib/python3.9/site-packages/pandas/core/indexing.py:1817: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(loc, value, pi)


unnamed    zip      n_lat       n_lon customer_id first_name last_name  \
26       26  94005  37.682657 -122.411316        7172   Francois    Farish   

           street  louvein_community      city  central_node  
26  1 Texas Trail               6860  Brisbane             1

In [344]:
temp3_df = central_df.loc[central_df['central_node'] == 1]
temp3_df

unnamed    zip      n_lat       n_lon customer_id first_name last_name  \
26       26  94005  37.682657 -122.411316        7172   Francois    Farish   

           street  louvein_community      city  central_node  
26  1 Texas Trail               6860  Brisbane             1

### Export to CSV

In [346]:
import csv
central_df.to_csv("degree_centrality.csv")

# Running the Minimum Spanning Tree (MST) on Sub-Group

## MST approximately solves the Traveling Salesman Problem. We want to be greedy and minimize the path the drone is traveling as it delivers packages

### Load the Customer Postgres Table

In [28]:
rollback_before_flag = True
rollback_after_flag = True

query = """


select * 
from customer_clusters


"""

customer_clusters_df =  my_select_query_pandas(query, rollback_before_flag, rollback_after_flag)
customer_clusters_df

unnamed    zip      n_lat       n_lon customer_id first_name last_name  \
0           0  94002  37.520606 -122.298226        8103      Karil     Gives   
1           1  94002  37.513840 -122.289873        8100      Mercy  Blunsden   
2           2  94002  37.510353 -122.301011        8101      Levey     Duval   
3           3  94002  37.514176 -122.306404        8102     Margot  MacGiany   
4           4  94005  37.682348 -122.406707        7158    Malissa     Latek   
...       ...    ...        ...         ...         ...        ...       ...   
8133     8133  94973  38.006360 -122.638831        8098      Luisa   Symcoxe   
8134     8134  94973  38.017764 -122.637123        8099     Adella   Buscher   
8135     8135  94973  38.003338 -122.627826        8094      Raviv   Pierton   
8136     8136  94973  38.011278 -122.641591        8093      Lemmy  Ettridge   
8137     8137  94973  38.008756 -122.641346        8095      Emmet   Phippin   

                      street  louvein_community      city  
0           458 Welch Avenue               7894   Belmont  
1          173 Fairview Pass               7891   Belmont  
2             512 Melby Hill               7892   Belmont  
3         12 Fordem Crossing               7893   Belmont  
4       8346 Fieldstone Park               6860  Brisbane  
...                      ...                ...       ...  
8133     291 Thompson Street               7884  Woodacre  
8134     20 Scofield Parkway               7888  Woodacre  
8135     5739 Holmberg Point               7883  Woodacre  
8136         24 Dahle Circle               7884  Woodacre  
8137  78379 Fieldstone Trail               7884  Woodacre  

[8138 rows x 10 columns]

In [29]:
central_df = customer_clusters_df.loc[customer_clusters_df['louvein_community'] == 6860]
central_df

unnamed    zip      n_lat       n_lon customer_id first_name    last_name  \
4         4  94005  37.682348 -122.406707        7158    Malissa        Latek   
9         9  94005  37.683216 -122.409611        7189       Kaja     Killiner   
10       10  94005  37.682674 -122.414409        7188     Trever         Wais   
12       12  94005  37.683365 -122.407019        7186     Lucius        Gawne   
17       17  94005  37.686030 -122.410622        7181     Fraser       Vasser   
18       18  94005  37.687203 -122.409959        7180     Candie        Dayne   
25       25  94005  37.682012 -122.403878        7173    Joshuah    MacFadzan   
26       26  94005  37.682657 -122.411316        7172   Francois       Farish   
27       27  94005  37.681886 -122.416236        7171     Byrann      Feechum   
30       30  94005  37.682597 -122.398976        7168      Ashly       Lindup   
32       32  94005  37.679975 -122.412504        7166       Riva  Schoolcroft   
34       34  94005  37.682768 -122.412029        7164     Mellie    Berriball   
36       36  94005  37.680983 -122.403332        7162    Laurena        Calan   
41       41  94005  37.685899 -122.410254        7155      Sonya        Puzey   

                    street  louvein_community      city  
4     8346 Fieldstone Park               6860  Brisbane  
9   2122 Eagle Crest Plaza               6860  Brisbane  
10   13540 Manitowish Lane               6860  Brisbane  
12       6586 Dorton Alley               6860  Brisbane  
17     6313 Warbler Circle               6860  Brisbane  
18           807 Roth Road               6860  Brisbane  
25      135 Di Loreto Park               6860  Brisbane  
26           1 Texas Trail               6860  Brisbane  
27            5 Tony Plaza               6860  Brisbane  
30   47 Fieldstone Parkway               6860  Brisbane  
32   64581 Atwood Junction               6860  Brisbane  
34        85524 Carey Lane               6860  Brisbane  
36     75869 Mccormick Way               6860  Brisbane  
41       3927 Spenser Pass               6860  Brisbane

### Recreate Graph Database 

In [30]:
my_neo4j_wipe_out_database()
my_neo4j_number_nodes_relationships()

-------------------------
  Nodes: 0
  Relationships: 0
-------------------------


### Recreate Customer Nodes

In [33]:
import time
start_time = time.time()


for ind in central_df.index:
    
    customer = central_df['customer_id'][ind]
    
    my_neo4j_create_customer_node(customer)
    
print(time.time() - start_time, " seconds")

0.35352540016174316  seconds


### Recreate Relationships

In [34]:
import time
start_time = time.time()


block_size = 0.24 #miles
for ind in central_df.index:
    point = (central_df['n_lat'][ind], central_df['n_lon'][ind])
    left, right, top, bottom = my_calculate_block(point, block_size) #tryy 0.25 mile for now
    
    connection.rollback()
    query = "select customer_id from customer_clusters"
    query += " where n_lat >= " + str(bottom[0])
    query += " and n_lat <= " + str(top [0])
    query += " and n_lon >= " + str(left[1])
    query += " and n_lon <= " + str(right[1])
    query += " order by 1 "
    cursor.execute(query)
    connection.rollback()
    rows = cursor.fetchall()
    print("*********"+str(ind)+"*********")
    print("running time ", time.time() - start_time, "seconds")
    for row in rows:        
        if row[0] != central_df['customer_id'][ind]:
            cid = str(row[0])            
            l_df = central_df.loc[central_df['customer_id'] == cid]
            point_1 = ( central_df['n_lat'][ind], central_df['n_lon'][ind])
            point_2 = ( float(l_df['n_lat']), float(l_df['n_lon']) )
            weight =  my_calculate_distance(point_1, point_2)
            my_neo4j_create_relationship_one_customer(central_df['customer_id'][ind], row[0], weight)
            print("created relationship between ", central_df['customer_id'][ind], "and ", row[0])

print("total execution time ", time.time() - start_time, "seconds")

*********4*********
running time  0.0025229454040527344 seconds
created relationship between  7158 and  7162
created relationship between  7158 and  7173
created relationship between  7158 and  7186
created relationship between  7158 and  7189
*********9*********
running time  0.10697126388549805 seconds
created relationship between  7189 and  7155
created relationship between  7189 and  7158
created relationship between  7189 and  7164
created relationship between  7189 and  7166
created relationship between  7189 and  7172
created relationship between  7189 and  7181
created relationship between  7189 and  7186
*********10*********
running time  0.1737682819366455 seconds
created relationship between  7188 and  7155
created relationship between  7188 and  7164
created relationship between  7188 and  7166
created relationship between  7188 and  7171
created relationship between  7188 and  7172
created relationship between  7188 and  7181
*********12*********
running time  0.2389309406

In [35]:
my_neo4j_number_nodes_relationships()

-------------------------
  Nodes: 14
  Relationships: 70
-------------------------


### Apply MST Algorithm To It, create graph and then run algorithm

In [40]:
def my_neo4j_wipe_out_mst_relationships():
    "wipe out mst relationships"
    
    query = "match (node)-[relationship:MST]->() delete relationship"
    session.run(query)

In [41]:
my_neo4j_wipe_out_mst_relationships()

### Creating MST graph

In [42]:
query = "CALL gds.graph.drop('ds_graph', false)"
session.run(query)

query = """

CALL gds.graph.project('ds_graph', 'Customer', 
                        {
                            LINK: {
                                properties: 'weight',
                                orientation: 'UNDIRECTED'
                            }
                        }
                       )

"""

session.run(query)

## Below is the Minimum Spanning Tree


In [45]:
query = """

MATCH path = (n:Customer {name: $source})-[:MST*]-()
WITH relationships(path) AS rels
UNWIND rels AS rel
WITH DISTINCT rel AS rel
RETURN startNode(rel).name AS source, endNode(rel).name AS destination, rel.writeCost AS cost

"""
#what should be the source? Its customer_id, 7172, based on centrality algorithm
source = "7172"

mst_df = my_neo4j_run_query_pandas(query, source=source)

In [46]:
mst_df

source destination       cost
0    7172        7186   4.157830
1    7186        7162   3.839652
2    7162        7168   3.796061
3    7162        7158   4.817943
4    7186        7181   3.707173
5    7181        7164   4.204759
6    7164        7171   4.193171
7    7171        7166   4.109478
8    7166        7189   3.649562
9    7181        7188   3.216641
10   7188        7155   3.141258
11   7155        7180  10.949533
12   7186        7173   5.106573

### Lets Only Keep the MST relationships with cost as weight 

In [57]:
my_neo4j_wipe_out_database()
my_neo4j_number_nodes_relationships()

-------------------------
  Nodes: 0
  Relationships: 0
-------------------------


### Create nodes

In [58]:
import time
start_time = time.time()

node_created = []
for ind in mst_df.index:
    customer = mst_df['source'][ind] 
    if customer not in node_created:
        my_neo4j_create_customer_node(customer)
        node_created.append(customer)

#print("nodes created: ", node_created)
for ind2 in mst_df.index:
    destination = mst_df['destination'][ind2] 
    if destination not in node_created:
        my_neo4j_create_customer_node(destination)
        #print("destination: ", destination)
    
    
print(time.time() - start_time, " seconds", my_neo4j_number_nodes_relationships())

-------------------------
  Nodes: 14
  Relationships: 0
-------------------------
0.0545659065246582  seconds None


### Create relationships
### Provides a better image of the MST 

In [59]:
for ind in mst_df.index:
    my_neo4j_create_relationship_one_customer(mst_df['source'][ind], mst_df['destination'][ind], mst_df['cost'][ind])
    #print("created relationship between ", mst_df['source'][ind], "and ", mst_df['destination'][ind])

print("total execution time ", time.time() - start_time, "seconds \n", my_neo4j_number_nodes_relationships() )

-------------------------
  Nodes: 14
  Relationships: 13
-------------------------
total execution time  8.488497972488403 seconds 
 None


### Export to CSV file for later use

In [60]:
mst_df.to_csv("minimum_spanning_tree.csv")

# Do Mapping Visualization in Another File